In [50]:
!pip install fasttext
!pip install spacy
!pip install gensim
!pip install google.cloud
!python -m spacy download en_core_web_sm
!python -m spacy download es_core_news_sm
!python -m spacy download de_core_news_sm
!pip install stanfordnlp

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.8/12.8 MB 14.2 MB/s eta 0:00:0000:0100:01


✔ Download and installation successful
You can now load the package via spacy.load('en_core_web_sm')
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.9/12.9 MB 13.8 MB/s eta 0:00:0000:0100:01
✔ Download and installation successful
You can now load the package via spacy.load('es_core_news_sm')
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 14.6/14.6 MB 24.9 MB/s eta 0:00:0000:0100:01


✔ Download and installation successful
You can now load the package via spacy.load('de_core_news_sm')
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 158.8/158.8 kB 2.2 MB/s eta 0:00:00a 0:00:01


In [55]:
!pip install stanza

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 802.5/802.5 kB 7.7 MB/s eta 0:00:00a 0:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 361.8/361.8 kB 12.6 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
  Created wheel for emoji: filename=emoji-2.7.0-py2.py3-none-any.whl size=356563 sha256=392fd5fa9abb2d6b318b46ee170bbe93d2c27ae12bbc67364ef3677499831e3c
  Stored in directory: /Users/georgeflint/Library/Caches/pip/wheels/74/c3/73/5cbb3586e57ed5d7fecf00b3a8f34972444bd401c0136c4d6c
Successfully built emoji


In [32]:
import sys
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
import math
import numpy as np
import fasttext
import spacy
from gensim.models.fasttext import load_facebook_model
from google.cloud import translate_v2 as translate
import pandas as pd
import os

In [10]:
bar = '---------------------------------------------------------------'
print(bar)

os.environ['GOOGLE_APPLICATION_CREDENTIALS'] = 'sacred-courier-393218-25b0abedbcc7.json'

# Google translate client
translate_client = translate.Client()
print("translator - loaded")

en_model_path = 'cc.en.300.bin'
es_model_path = 'cc.es.300.bin'
de_model_path = 'cc.de.300.bin'
en = load_facebook_model(en_model_path)
print("en - loaded")
es = load_facebook_model(es_model_path)
print("es - loaded")
de = load_facebook_model(de_model_path)
print("de - loaded")
print(bar)

models = {"en": en, "es": es, "de": de}

---------------------------------------------------------------
translator - loaded
en - loaded
es - loaded
de - loaded
---------------------------------------------------------------


In [46]:
# functions
def translate_word(word, target_language):
    """Function to translate a word to the target language."""
    result = translate_client.translate(word, target_language=target_language)
    return result['translatedText']
def cossim(model, vector1, vector2):
    """Return cosine similarity between vec1 and vec2"""
    return model.wv.cosine_similarities(vector1, [vector2])[0]
def euclid(vec1, vec2):
    vec1, vec2 = np.array(vec1), np.array(vec2)
    return np.linalg.norm(vec1 - vec2)
def get(model, word):
    """Return word embedding for word as in model"""
    return model.wv.get_vector(word)
def is_adjective(word):
    if language.lower() == 'en':
        nlp = spacy.load('en_core_web_sm')
    elif language.lower() == 'es':
        nlp = spacy.load('es_core_news_sm')
    elif language.lower() == 'de':
        nlp = spacy.load('de_core_news_sm')
    else:
        return False
    doc = nlp(word)
    return any(token.pos_ == 'ADJ' for token in doc)
def filter_word(word):
    word = word.lower()
    return not any(filter in word for filter in filters)

genders = {
    "en":[
        'man',
        'woman',
        ],
    "es":[
        'hombre',
        'mujer'
        ],
    "de":[
        'Mann',
        'Frau',
        ],
}
neighbors = {
    "en":{
    },
    "es":{
    },
    "de":{
    }
}
filters = [
    "-year-old",
     ".",
    "jährige",
    
    "--",
    "-",
    "."
]
filters.extend([str(char) for char in range(10)])
print(filters)
print(bar)

['-year-old', '.', 'jährige', '--', '-', '.', '0', '1', '2', '3', '4', '5', '6', '7', '8', '9']
---------------------------------------------------------------


In [48]:
for language in genders:
    print(f'language - {language}')
    print(bar*2)
    for i, target in enumerate(genders[language]):
        print(f'target - {target}')
        print(bar*2)
        neighbors[language][target] = []
        neighborhood = models[language].wv.most_similar(
            positive=[target], 
            negative=[genders[language][1-i][0]],
            topn=14000
        )
        for neighbor in neighborhood:
            print(neighbor)
            word = neighbor[0]
            if filter_word(word) and is_adjective(word):
                print(bar)
                print(f'{word} - passed')
                print(bar)
                neighbors[language][target].append(word)

print(neighbors)
print(bar)

# initialize a DataFrame to store results
df = pd.DataFrame(columns=["PART OF SPEECH", "LANGUAGE", "ASSOCIATION/GRAMMATICAL GENDER", "WORD", "TRANSLATION", "cosine_similarity_to_target"])
print('dataframe - initialized')

# go through the neighbors and add data to the DataFrame
for language in neighbors:
    for word, neighborhood in neighbors[language].items():
        for neighbor in neighborhood:
            # translate the word to English if it is not already
            translation = translate_word(neighbor, 'en') if language != 'en' else neighbor
            
            # get gender
            gender = 'masculine' if word in ['man', 'hombre', 'Mann'] else 'feminine'
            
            # get cosine similarity
            cosine_similarity = cossim(models[language], get(models[language], word), get(models[language], neighbor))
            
            # add data to the DataFrame
            df = df._append({
                "PART OF SPEECH": "Adjective",
                "LANGUAGE": language,
                "ASSOCIATION/GRAMMATICAL GENDER": gender,
                "WORD": neighbor,
                "TRANSLATION": translation,
                "cosine_similarity_to_target": cosine_similarity
            }, ignore_index=True) # type: ignore  **(this is for pylance thinking this this df method is an error)**

# write DataFrame to a CSV file
df.to_csv('results.csv', index=False)
print('dataframe - offloaded to csv')

language - en
---------------------------------------------------------------
target - man
---------------------------------------------------------------
('woman', 0.5372059941291809)
('man.He', 0.5079009532928467)
('woman.He', 0.4939799904823303)
('man.One', 0.48897117376327515)
('man.The', 0.48449596762657166)
('man.It', 0.47946926951408386)
('man--he', 0.4743648171424866)
('man.When', 0.4652802348136902)
('man.A', 0.4598807990550995)
('man.That', 0.4565693140029907)
('woman.A', 0.4557209610939026)
('man.Then', 0.4538215100765228)
('man.But', 0.45110005140304565)
('woman--and', 0.45011672377586365)
('man.She', 0.44855278730392456)
('man--the', 0.4467545747756958)
('man--and', 0.4399055540561676)
('man.And', 0.43937376141548157)
('man.If', 0.43816959857940674)
('gentleman', 0.43682461977005005)
('man--a', 0.433133065700531)
('woman.When', 0.42904797196388245)
('woman.It', 0.4288174510002136)
('woman.They', 0.42389488220214844)
('man.What', 0.42241019010543823)
('man.So', 0.4207956194

('23-year-old', 0.33029603958129883)
('fella', 0.3301428258419037)
('servant', 0.3293801546096802)
('living.He', 0.3291132152080536)
('monkey-man', 0.32904377579689026)
('men.As', 0.3283878266811371)
('man.2', 0.3282296657562256)
('manthat', 0.32812997698783875)
('everyman', 0.3277013897895813)
('man.Of', 0.3276861608028412)
('83-year-old', 0.32764682173728943)
('wife.A', 0.32763367891311646)
('manliest', 0.3276246190071106)
---------------------------------------------------------------
manliest - passed
---------------------------------------------------------------
('girl.A', 0.3274649977684021)
('womanYou', 0.3272661566734314)
('hero', 0.3272104859352112)
('strong.He', 0.3266791105270386)
('teen-ager', 0.3266746401786804)
('men.That', 0.3260141611099243)
('anyone.He', 0.3257175385951996)
('man-servant', 0.32545480132102966)
('passerby', 0.32509905099868774)
('red-blooded', 0.3250308334827423)
('sandy-haired', 0.3249898850917816)
('men.For', 0.32497718930244446)
('truth.He', 0.32476

('silver-haired', 0.2996060848236084)
('theman', 0.29952195286750793)
('name.He', 0.29946792125701904)
('place.He', 0.29944318532943726)
('friend--a', 0.2994164228439331)
('generation.He', 0.2992308437824249)
('wo-man', 0.2992132604122162)
('wife.When', 0.29912158846855164)
('forty-eight-year-old', 0.298753023147583)
('godliest', 0.2986900806427002)
('friendof', 0.298539400100708)
('Irishwoman', 0.2983498275279999)
('boy.When', 0.29809319972991943)
('priest-like', 0.2979816496372223)
('people--a', 0.29782527685165405)
('men.My', 0.29781877994537354)
('anold', 0.2977399230003357)
('acquaintance', 0.29768136143684387)
('image-bearer', 0.29763028025627136)
('lion-hearted', 0.2974618375301361)
('lover.The', 0.2974291443824768)
('father-figure', 0.2973203659057617)
('God-fearing', 0.2973055839538574)
('faith.He', 0.29708489775657654)
('Britain.He', 0.29671216011047363)
('man-like', 0.2966737449169159)
('fifth-richest', 0.2966347634792328)
('86-year-old', 0.2965218126773834)
('wife.This', 0.

---------------------------------------------------------------
chivalrous - passed
---------------------------------------------------------------
('39-years-old', 0.28546324372291565)
('adventurer', 0.2853185534477234)
('broad-chested', 0.2852909564971924)
('23-years-old', 0.28528693318367004)
('school-master', 0.28522247076034546)
('fellow-passenger', 0.2851797640323639)
('perfect.He', 0.2851671278476715)
('you.Someone', 0.2850617468357086)
('stop.He', 0.28502950072288513)
('father-of-three', 0.2849990129470825)
('saved.The', 0.2849637567996979)
('robber', 0.2849189341068268)
('womenI', 0.28490710258483887)
('thirty-five-year-old', 0.28487589955329895)
('manSo', 0.28473004698753357)
('ballplayer', 0.28469526767730713)
('honourable', 0.2845780849456787)
---------------------------------------------------------------
honourable - passed
---------------------------------------------------------------
('not.He', 0.2845526337623596)
('15-year-old', 0.2845328450202942)
('self-respecting',

('law-giver', 0.2765965759754181)
('heart.That', 0.2765669524669647)
('wife', 0.2764858603477478)
('manI', 0.27646327018737793)
('friend.They', 0.2764541804790497)
('law-maker', 0.2764175832271576)
('cart-horse', 0.2763940989971161)
('people.He', 0.2763865888118744)
('girland', 0.27637165784835815)
('nameis', 0.2763645350933075)
('62-year', 0.2763534188270569)
('question.He', 0.2762935757637024)
('hispeople', 0.2762524485588074)
('idea.He', 0.2762041687965393)
('someone', 0.27618691325187683)
('thirty-six-year-old', 0.2761651873588562)
('start.He', 0.2761574685573578)
('guy.Well', 0.2761056125164032)
('religion.He', 0.27596381306648254)
('thug', 0.2759504020214081)
('ditch-digger', 0.2759033739566803)
('person.That', 0.2757677137851715)
('man-God', 0.2757558226585388)
('father.The', 0.275748610496521)
('manA', 0.27570655941963196)
('metrosexual', 0.2756434381008148)
---------------------------------------------------------------
metrosexual - passed
------------------------------------

...

('Besiegter', 0.2677857279777527)
('Teammädels', 0.26778173446655273)
('GmbHFrau', 0.26778045296669006)
('Njáll', 0.2677803039550781)
('tragischerweise', 0.267774373292923)
('Kitzhaber', 0.26776352524757385)
('Steinke', 0.26776066422462463)
('Besiedlungszeit', 0.26775792241096497)
('Untermietern', 0.26775556802749634)
('Schlussmachen', 0.267755389213562)
('niemands', 0.26775360107421875)
('Alvira', 0.26775237917900085)
('seelenverwandten', 0.26774856448173523)
('Riesebrodt', 0.2677442729473114)
('Strohfrau', 0.26774004101753235)
('Schulpfleger', 0.2677399218082428)
('Erkenntnislage', 0.26773837208747864)
('Brasche', 0.26773500442504883)
('Schaubert', 0.2677346169948578)
('Fölster', 0.2677341401576996)
('Dieckmanns', 0.26773378252983093)
('Sportwaffe', 0.26772671937942505)
('Kanze', 0.26772481203079224)
('Schlossverwalters', 0.26771894097328186)
('Erblindeten', 0.26771822571754456)
('Werbener', 0.2677169144153595)
('Männerberuf', 0.2677168846130371)
('Comicumsetzung', 0.2677094638347626

('Glücklichere', 0.2672199308872223)
('willensschwachen', 0.26721781492233276)
('Schützenmeisterin', 0.26721757650375366)
('Schulleitung', 0.26721668243408203)
('Unterhält', 0.26721641421318054)
('habende', 0.26721519231796265)
('geburtstagskind', 0.2672094702720642)
('Hausmeiers', 0.26720234751701355)
('Gefühlsregung', 0.2672012150287628)
('seinUnd', 0.2671999931335449)
('Riccardos', 0.2671974301338196)
('Talena', 0.2671962380409241)
('Haupternährer', 0.26719072461128235)
('Magnhild', 0.2671900987625122)
('Kastning', 0.2671884000301361)
('inkontinente', 0.2671869993209839)
('Kaufmannswitwe', 0.2671799957752228)
('hannelore', 0.26717686653137207)
('Irmas', 0.26717662811279297)
('Grippeinfektion', 0.26717543601989746)
('Mulattinnen', 0.2671750485897064)
('Großelternteils', 0.2671738564968109)
('Minna', 0.26716938614845276)
('FrauWertvolle', 0.2671664357185364)
('Kammerjägern', 0.2671636641025543)
('Ururgroßvaters', 0.2671605050563812)
('Liebespositionen', 0.26715749502182007)
('Bohlande

('fünfzehnjähriges', 0.26660361886024475)
('Roelle', 0.266598105430603)
('Jesses', 0.2665950655937195)
('Collegestudentin', 0.26659300923347473)
('Unverheirateten', 0.26658856868743896)
('Taria', 0.26658424735069275)
('Gutsbesitzers', 0.2665841281414032)
('Charayron', 0.2665836811065674)
('Ex-Affäre', 0.2665797770023346)
('Mädchenspiel', 0.26657846570014954)
('sturzbetrunkene', 0.2665748596191406)
---------------------------------------------------------------
sturzbetrunkene - passed
---------------------------------------------------------------
('Brigide', 0.26657426357269287)
('Verling', 0.2665715515613556)
('Frisöse', 0.2665705382823944)
('großmütige', 0.2665674686431885)
---------------------------------------------------------------
großmütige - passed
---------------------------------------------------------------
('Missionarsschule', 0.2665671110153198)
('Theaterautorin', 0.26656681299209595)
('Plektrud', 0.26656675338745117)
('Gritter', 0.2665582597255707)
('Hilfesuchender', 

('Émilienne', 0.2661125957965851)
('Fahrzeuginsasse', 0.26611196994781494)
('Vierzigern', 0.2661118507385254)
('schwindelte', 0.26610150933265686)
('Frauenwelt', 0.26610085368156433)
('Frauendemonstration', 0.2660995125770569)
('Dietmut', 0.26609042286872864)
('Wellness-Behandlung', 0.26608943939208984)
('Sonnenscheinchen', 0.2660863697528839)
('Diplomandin', 0.26608482003211975)
('Idamante', 0.26608407497406006)
('Sexfantasie', 0.26608380675315857)
('Calvis', 0.2660757601261139)
('Polizeiinformationen', 0.2660743296146393)
('Verwandte', 0.2660697400569916)
('Marijane', 0.2660650312900543)
('Kanzlerschaft', 0.2660641670227051)
('Morgenthal', 0.2660612165927887)
('NDR-Redakteur', 0.26606085896492004)
('Katherlieschen', 0.26606062054634094)
('Bleibt-Entscheidung', 0.26606032252311707)
('Schandmaske', 0.2660517394542694)
('Cristin', 0.2660512328147888)
('Elektronikzange', 0.2660501301288605)
('Gastfreunde', 0.26604577898979187)
('Kolbert', 0.26604533195495605)
('Beckenbodenübungen', 0.266

dataframe - offloaded to csv


In [51]:
import stanfordnlp

# Download models for English, Spanish, and German
stanfordnlp.download('en')
stanfordnlp.download('es')
stanfordnlp.download('de')

# Set up pipelines for each language
nlp_en = stanfordnlp.Pipeline(lang='en')
nlp_es = stanfordnlp.Pipeline(lang='es')
nlp_de = stanfordnlp.Pipeline(lang='de')

Using the default treebank "en_ewt" for language "en".
Would you like to download the models for: en_ewt now? (Y/n)
y

Default download directory: /Users/georgeflint/stanfordnlp_resources
Hit enter to continue or type an alternate directory.


Download location: /Users/georgeflint/stanfordnlp_resources/en_ewt_models.zip


100%|████████████████████████████████████████| 235M/235M [00:41<00:00, 5.67MB/s]



Download complete.  Models saved to: /Users/georgeflint/stanfordnlp_resources/en_ewt_models.zip
Extracting models file for: en_ewt
Cleaning up...Done.
Using the default treebank "es_ancora" for language "es".
Would you like to download the models for: es_ancora now? (Y/n)
y

Default download directory: /Users/georgeflint/stanfordnlp_resources
Hit enter to continue or type an alternate directory.


Download location: /Users/georgeflint/stanfordnlp_resources/es_ancora_models.zip


100%|████████████████████████████████████████| 226M/226M [01:10<00:00, 3.21MB/s]



Download complete.  Models saved to: /Users/georgeflint/stanfordnlp_resources/es_ancora_models.zip
Extracting models file for: es_ancora
Cleaning up...Done.
Using the default treebank "de_gsd" for language "de".
Would you like to download the models for: de_gsd now? (Y/n)
y

Default download directory: /Users/georgeflint/stanfordnlp_resources
Hit enter to continue or type an alternate directory.


Download location: /Users/georgeflint/stanfordnlp_resources/de_gsd_models.zip


100%|████████████████████████████████████████| 229M/229M [00:39<00:00, 5.76MB/s]



Download complete.  Models saved to: /Users/georgeflint/stanfordnlp_resources/de_gsd_models.zip
Extracting models file for: de_gsd
Cleaning up...Done.
Use device: cpu
---
Loading: tokenize
With settings: 
{'model_path': '/Users/georgeflint/stanfordnlp_resources/en_ewt_models/en_ewt_tokenizer.pt', 'lang': 'en', 'shorthand': 'en_ewt', 'mode': 'predict'}
---
Loading: pos
With settings: 
{'model_path': '/Users/georgeflint/stanfordnlp_resources/en_ewt_models/en_ewt_tagger.pt', 'pretrain_path': '/Users/georgeflint/stanfordnlp_resources/en_ewt_models/en_ewt.pretrain.pt', 'lang': 'en', 'shorthand': 'en_ewt', 'mode': 'predict'}
---
Loading: lemma
With settings: 
{'model_path': '/Users/georgeflint/stanfordnlp_resources/en_ewt_models/en_ewt_lemmatizer.pt', 'lang': 'en', 'shorthand': 'en_ewt', 'mode': 'predict'}
Building an attentional Seq2Seq model...
Using a Bi-LSTM encoder
Using soft attention for LSTM.
Finetune all embeddings.
[Running seq2seq lemmatizer with edit classifier]
---
Loading: dep

In [52]:
def is_adjective_stanfordnlp(word, language):
    """Return whether the word is an adjective for the specified language."""
    
    # Select appropriate model
    if language.lower() == 'en':
        nlp = nlp_en
    elif language.lower() == 'es':
        nlp = nlp_es
    elif language.lower() == 'de':
        nlp = nlp_de
    else:
        raise ValueError(f"Unsupported language: {language}")
    
    # Process the word
    doc = nlp(word)
    
    # Check if the word is an adjective
    return any(word.upos == 'ADJ' for sentence in doc.sentences for word in sentence.words)


In [58]:
# Load initial results
results_df = pd.read_csv('results.csv')
print('dataframe - loaded')

# Initialize empty DataFrame for filtered results
filtered_df = pd.DataFrame()

for language in ['en', 'es', 'de']:
    print(f'language - {language}')
    print(bar*2)
    for gender in ['masculine', 'feminine']:
        temp_df = results_df[(results_df['LANGUAGE'] == language) & (results_df['ASSOCIATION/GRAMMATICAL GENDER'] == gender)]
        temp_df = temp_df[temp_df['WORD'].apply(is_adjective_stanfordnlp, args=(language,))]
        temp_df = temp_df.sort_values('cosine_similarity_to_target', ascending=False).head(1000)
        filtered_df = pd.concat([filtered_df, temp_df])

# Save the filtered results
filtered_df.to_csv('truncated_results.csv', index=False)
print('dataframe - processed and offloaded to csv')

dataframe - loaded
language - en
------------------------------------------------------------------------------------------------------------------------------
language - es
------------------------------------------------------------------------------------------------------------------------------
language - de
------------------------------------------------------------------------------------------------------------------------------
dataframe - processed and offloaded to csv


In [57]:
import stanza
import pandas as pd

# Download models for English, Spanish, and German
stanza.download('en')
stanza.download('es')
stanza.download('de')

# Set up pipelines for each language
nlp_en = stanza.Pipeline('en')
nlp_es = stanza.Pipeline('es')
nlp_de = stanza.Pipeline('de')

def is_adjective_stanza(word, language):
    """Return whether the word is an adjective for the specified language."""
    
    # Select appropriate model
    if language.lower() == 'en':
        nlp = nlp_en
    elif language.lower() == 'es':
        nlp = nlp_es
    elif language.lower() == 'de':
        nlp = nlp_de
    else:
        raise ValueError(f"Unsupported language: {language}")
    
    # Process the word
    doc = nlp(word)
    
    # Check if the word is an adjective
    return any(word.upos == 'ADJ' for sentence in doc.sentences for word in sentence.words)

2023-07-26 15:05:25 INFO: Downloading default packages for language: en (English) ...
2023-07-26 15:05:28 INFO: File exists: /Users/georgeflint/stanza_resources/en/default.zip
2023-07-26 15:05:31 INFO: Finished downloading models and saved to /Users/georgeflint/stanza_resources.


2023-07-26 15:05:31 INFO: Downloading default packages for language: es (Spanish) ...
2023-07-26 15:05:33 INFO: File exists: /Users/georgeflint/stanza_resources/es/default.zip
2023-07-26 15:05:36 INFO: Finished downloading models and saved to /Users/georgeflint/stanza_resources.


2023-07-26 15:05:36 INFO: Downloading default packages for language: de (German) ...
2023-07-26 15:05:39 INFO: File exists: /Users/georgeflint/stanza_resources/de/default.zip
2023-07-26 15:05:42 INFO: Finished downloading models and saved to /Users/georgeflint/stanza_resources.
2023-07-26 15:05:42 INFO: Checking for updates to resources.json in case models have been updated.  Note: this behavior can be turned off with download_method=None or download_method=DownloadMethod.REUSE_RESOURCES


2023-07-26 15:05:44 INFO: Loading these models for language: en (English):
| Processor    | Package   |
----------------------------
| tokenize     | combined  |
| pos          | combined  |
| lemma        | combined  |
| constituency | wsj       |
| depparse     | combined  |
| sentiment    | sstplus   |
| ner          | ontonotes |

2023-07-26 15:05:44 INFO: Using device: cpu
2023-07-26 15:05:44 INFO: Loading: tokenize
2023-07-26 15:05:44 INFO: Loading: pos
2023-07-26 15:05:44 INFO: Loading: lemma
2023-07-26 15:05:44 INFO: Loading: constituency
2023-07-26 15:05:45 INFO: Loading: depparse
2023-07-26 15:05:45 INFO: Loading: sentiment
2023-07-26 15:05:45 INFO: Loading: ner
2023-07-26 15:05:46 INFO: Done loading processors!
2023-07-26 15:05:46 INFO: Checking for updates to resources.json in case models have been updated.  Note: this behavior can be turned off with download_method=None or download_method=DownloadMethod.REUSE_RESOURCES


2023-07-26 15:05:47 INFO: Loading these models for language: es (Spanish):
| Processor    | Package  |
---------------------------
| tokenize     | ancora   |
| mwt          | ancora   |
| pos          | ancora   |
| lemma        | ancora   |
| constituency | combined |
| depparse     | ancora   |
| sentiment    | tass2020 |
| ner          | conll02  |

2023-07-26 15:05:47 INFO: Using device: cpu
2023-07-26 15:05:47 INFO: Loading: tokenize
2023-07-26 15:05:47 INFO: Loading: mwt
2023-07-26 15:05:47 INFO: Loading: pos
2023-07-26 15:05:48 INFO: Loading: lemma
2023-07-26 15:05:48 INFO: Loading: constituency
2023-07-26 15:05:48 INFO: Loading: depparse
2023-07-26 15:05:48 INFO: Loading: sentiment
2023-07-26 15:05:48 INFO: Loading: ner
2023-07-26 15:05:49 INFO: Done loading processors!
2023-07-26 15:05:49 INFO: Checking for updates to resources.json in case models have been updated.  Note: this behavior can be turned off with download_method=None or download_method=DownloadMethod.REUSE_RESOUR

2023-07-26 15:05:51 INFO: Loading these models for language: de (German):
| Processor | Package      |
----------------------------
| tokenize  | gsd          |
| mwt       | gsd          |
| pos       | gsd          |
| lemma     | gsd          |
| depparse  | gsd          |
| sentiment | sb10k        |
| ner       | germeval2014 |

2023-07-26 15:05:51 INFO: Using device: cpu
2023-07-26 15:05:51 INFO: Loading: tokenize
2023-07-26 15:05:51 INFO: Loading: mwt
2023-07-26 15:05:51 INFO: Loading: pos
2023-07-26 15:05:51 INFO: Loading: lemma
2023-07-26 15:05:51 INFO: Loading: depparse
2023-07-26 15:05:51 INFO: Loading: sentiment
2023-07-26 15:05:52 INFO: Loading: ner
2023-07-26 15:05:53 INFO: Done loading processors!


In [61]:
# Read the data from CSV file
control_data = pd.read_csv('CONTROL DATA.csv')

# Set of languages
languages = control_data['LANGUAGE'].unique()

# Set of target categories
target_categories = control_data['TARGET CATEGORY'].unique()

# Plotting
for lang in languages:
    fig, axs = plt.subplots(2, 2, figsize=(20, 20))
    axs = axs.flatten()  # flatten the axis array for easy iteration

    for i, target_category in enumerate(target_categories):
        subset = control_data[(control_data['LANGUAGE'] == lang) & (control_data['TARGET CATEGORY'] == target_category)]
        
        # Create a boxplot
        sns.boxplot(ax=axs[i], x='REFERENCE ASSOCIATION/GRAMMATICAL GENDER', y='COSINE SIMILARITY', hue='SUB-LIST', data=subset)
        axs[i].set_title(f"{target_category.capitalize()} - {lang}")
        axs[i].legend(loc='upper right')

    plt.tight_layout()
    plt.savefig(f"Control_Data_{lang}.png")
    plt.close()

NameError: name 'subset' is not defined